[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://drive.google.com/file/d/1yFljPVDZlBxiwOpd92UuYB-fs9nZPdn0/view?usp=sharing)

In [ ]:
!pip install -qU openai portkey-ai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 337.0/337.0 kB 2.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 405.9/405.9 kB 12.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.6/75.6 kB 2.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.5/12.5 MB 31.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.9/77.9 kB 2.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 2.2 MB/s eta 0:00:00


In [ ]:
from google.colab import userdata

OPENAI_API_KEY = userdata.get("OPENAI_API_KEY") ## replace it your OpenAI API key
PORTKEY_API_KEY = userdata.get("PORTKEY_API_KEY") ## grab your key from https://portkey.ai/

In [ ]:
from openai import OpenAI
from portkey_ai import PORTKEY_GATEWAY_URL, createHeaders
import random
from google.colab import userdata

client = OpenAI(
    api_key= OPENAI_API_KEY,
    base_url=PORTKEY_GATEWAY_URL,
    default_headers=createHeaders(
        provider="openai",
        api_key= PORTKEY_API_KEY,
    )
)

In [ ]:
def generate_plans(user_query, n=5):
    """Generate multiple plans using GPT-4o-Mini."""
    response = client.chat.completions.create(
        model="gpt-4o-mini",
        messages=[
            {"role": "system", "content": "You are a strategic reasoner. Given a user query, create a detailed plan to address it and then respond to the user. You will do so by using <thinking> and <response> tags. The user will only see what is in <response>, the <thinking> is just a scratchpad for you to figure out the best approach to satisfy the user's request. First, plan inside <thinking> tags, and then write your <response>."},
            {"role": "user", "content": user_query}
        ],
        n=n,
        temperature=0.7,
        max_tokens=500,
        stop=['</thinking>']
    )
    return [choice.message.content.replace('<thinking>', '') for choice in response.choices]

def evaluate_plans(plans, user_query):
    """Evaluate plans using a tournament ranking system."""
    def compare_plans(plan1, plan2):
        response = client.chat.completions.create(
            model="gpt-4o-mini",
            messages=[
                {"role": "system", "content": "You are a judge evaluating two plans. Choose the better plan based on effectiveness, feasibility, and relevance to the user's query."},
                {"role": "user", "content": f"User Query: {user_query}\n\nPlan 1: {plan1}\n\nPlan 2: {plan2}\n\nWhich plan is better? Respond with either '1' or '2'."}
            ],
            temperature=0.2,
            max_tokens=10
        )
        return 1 if response.choices[0].message.content.strip() == "1" else 2

    # Tournament ranking — to improve, run twice with swapped positions for each plan combo for greater precision, and parallelize for speed
    winners = plans
    while len(winners) > 1:
        next_round = []
        for i in range(0, len(winners), 2):
            if i + 1 < len(winners):
                winner = winners[i] if compare_plans(winners[i], winners[i+1]) == 1 else winners[i+1]
                next_round.append(winner)
            else:
                next_round.append(winners[i])
        winners = next_round

    return winners[0]

def generate_response(best_plan, user_query):
    """Generate the final response based on the best plan."""
    response = client.chat.completions.create(
        model="gpt-4o-mini",
        messages=[
            {"role": "system", "content": "You are a helpful assistant. Use the given plan to create a detailed and high-quality response to the user's query."},
            {"role": "user", "content": f"User Query: {user_query}\n\nPlan: {best_plan}\n\nGenerate a detailed response based on this plan."}
        ],
        temperature=0.5,
        max_tokens=2000
    )
    return response.choices[0].message.content

def improved_ai_output(user_query, num_plans=20):
    """Main function to improve AI output quality."""
    print("Generating plans...")
    plans = generate_plans(user_query, n=num_plans)

    print("Evaluating plans...")
    best_plan = evaluate_plans(plans, user_query)

    print("Generating final response...")
    final_response = generate_response(best_plan, user_query)

    return {
        "user_query": user_query,
        "best_plan": best_plan,
        "final_response": final_response
    }

if __name__ == "__main__":
    user_query = "How do I get a computer out of a bootloop?"
    result = improved_ai_output(user_query)

    print("\nUser Query:", result["user_query"])
    print("\nBest Plan:", result["best_plan"])
    print("\nFinal Response:", result["final_response"])

Generating plans...
Evaluating plans...
Generating final response...

User Query: How do I get a computer out of a bootloop?

Best Plan: 
1. Understand the nature of a bootloop: A bootloop occurs when a computer fails to complete the booting process, causing it to restart repeatedly. Common causes include software issues, corrupted files, hardware failures, or misconfigured settings.

2. Identify the type of computer: Determine whether the user is dealing with a Windows PC, Mac, or Linux system, as the troubleshooting steps may vary.

3. Outline common troubleshooting steps:
   - For Windows:
     a. Boot into Safe Mode: Restart the computer and press F8 or Shift + F8 during boot-up to access Safe Mode.
     b. Use Windows Recovery Environment: If Safe Mode fails, use a recovery USB or installation media to access repair options.
     c. Check for hardware issues: Reseat RAM and check hard drive connections.
     d. Perform System Restore: Use restore points to revert the system to a p

In [ ]:
if __name__ == "__main__":
    user_query = "What is the best way to lose weight?"
    result = improved_ai_output(user_query)

    print("\nUser Query:", result["user_query"])
    print("\nBest Plan:", result["best_plan"])
    print("\nFinal Response:", result["final_response"])

Generating plans...
Evaluating plans...
Generating final response...

User Query: What is the best way to lose weight?

Best Plan: 
1. Understand the user's context: The best weight loss methods can vary based on individual factors such as age, gender, current weight, health conditions, and lifestyle. To provide a comprehensive answer, I will focus on general principles, while also acknowledging that personal circumstances matter.

2. Identify key components of effective weight loss strategies:
   - Caloric deficit: Explain the importance of consuming fewer calories than the body expends.
   - Balanced diet: Emphasize the need for a healthy, balanced diet rich in whole foods, including fruits, vegetables, lean proteins, and whole grains.
   - Regular physical activity: Highlight the role of exercise in burning calories and improving overall health.
   - Behavior modification: Discuss the importance of making sustainable lifestyle changes rather than adopting temporary diets.
   - Hydra

## Telemetry with Portkey

42 API requests, 30.9k tokens, $0.0091 cost!

<img src="data:image/png;base64, ..." alt="Dashboard" height = "500">